# BERT NE recognition LOC/ORG/FACILITY

## 1)  Preprocess / format data

In [1]:
from __future__ import absolute_import, division, print_function

In [2]:
import codecs
import glob
import logging
import multiprocessing
import os
import pprint
import re
import keras
import nltk
import spacy

Using TensorFlow backend.


In [3]:
from nltk import ne_chunk, pos_tag
from nltk.tokenize import sent_tokenize, word_tokenize, PunktSentenceTokenizer
from nltk.corpus import stopwords
import gensim.models.word2vec as w2v
from gensim import logging
import sklearn.manifold
import numpy as np
import matplotlib.pyplot as plt
import pandas as  pd
import seaborn as sns
import pickle
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import json
from nltk.tokenize import WhitespaceTokenizer
from nltk.tokenize import MWETokenizer

In [4]:
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [5]:
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [6]:
import nltk
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/chantana/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

## 2) load keyword: LOC/ORG from text

In [337]:
word_files = ['./keywords/list_hotel.txt']
word_list_name = []
for word_file in word_files:
    with open(word_file) as f:
        lines = f.readlines()
    word_list2 = [x.strip() for x in lines] 
    
    word_list_name.extend(word_list2)
word_list_name[0:5]

['Petpimarn Boutique Resort',
 'Airport Suite Bangkok (Don Muang Airport)',
 'The Riche Residence',
 'Regent Home1 at Donmuang',
 'Charoenpong Apartment']

In [338]:
word_files = ['./keywords/facility.txt']
word_list_fac = []
for word_file in word_files:
    with open(word_file) as f:
        lines = f.readlines()
    word_list2 = [x.strip() for x in lines] 
    
    word_list_fac.extend(word_list2)
word_list_fac[0:5]

['24-hour Receptionist',
 'Laundry service',
 'Luggage storage',
 'Tours',
 'Parking']

In [339]:
word_hotels = ['./keywords/list_location.txt']
lists_location = []
for word_hotel in word_hotels:
    with open(word_hotel) as f:
        lines = f.readlines()
    lists_l= [x.strip() for x in lines] 
    
    lists_location.extend(lists_l)
lists_location[0:5]

['99/89 Moo 6',
 'VIPHAVADEE RANDSIT RD',
 '111/1 Soi Ngam Wong Wan 47 Yaek 1',
 '310/72 Soi Phaholyothin 67/1',
 '3/2899 Soi Yak']

In [340]:
#remove duplicates
def ordered_set(in_list):
    out_list = []
    added = set()
    for val in in_list:
        if not val in added:
            out_list.append(val)
            added.add(val)
    return out_list

In [341]:
word_list_name = ordered_set(word_list_name)

In [342]:
word_list_fac = ordered_set(word_list_fac)

In [343]:
word_location= ordered_set(lists_location)

word_locates = ['../keywords/hotel_location.txt']
word_hotel_location = []
for word_locate in word_locates:
    with open(word_locate) as f:
        lines = f.readlines()
    word_location2 = [x.strip() for x in lines] 
    
    word_hotel_location.extend(word_location2)
word_hotel_location[0:5]

In [344]:
mw_list = []
for x in word_list_name:
    ws = x.split() 
    if len(ws) > 1:
        tws = tuple(ws)
        mw_list.append(tws)
        

for x in word_location:
    ws = x.split() 
    if len(ws) > 1:
        tws = tuple(ws)
        mw_list.append(tws)
        

        
for x in word_list_fac:
    ws = x.split() 
    if len(ws) > 1:
        tws = tuple(ws)
        mw_list.append(tws)
         
            
mw_list = ordered_set(mw_list)
mw_list[0:5]

[('Petpimarn', 'Boutique', 'Resort'),
 ('Airport', 'Suite', 'Bangkok', '(Don', 'Muang', 'Airport)'),
 ('The', 'Riche', 'Residence'),
 ('Regent', 'Home1', 'at', 'Donmuang'),
 ('Charoenpong', 'Apartment')]

In [345]:
my_idx = {}
for i,w in enumerate(mw_list):
    my_idx[" ".join(w)] = i
print(len(my_idx))

35968


In [86]:
for i in mw_list:
    if i == ('M&A','Guesthouse'):
        print('found')
    if i == ('Central','Pattaya'):
        print('found')

found
found


In [88]:
mwe = MWETokenizer(mw_list,separator=' ')

In [89]:
reviews = pd.read_csv("./keywords/all_loc_fac.csv")

In [90]:
reviews.shape

(26541, 1)

In [91]:
reviews.head()

location
0  Staying at @ Home Executive Apartment is a goo...
1  Staying at @ Oasis Resort is a good choice whe...
2  Staying at @ T Boutique Hotel is a good choice...
3  Staying at AC Resort is a good choice when you...
4  Staying at Acqua Condominium is a good choice ...

In [92]:
reviews = reviews.dropna()
reviews = reviews.reset_index(drop=True)

In [93]:
def spans(txt):
    tokens=mwe.tokenize(word_tokenize(txt))
    offset = 0
    for token in tokens:
        offset = txt.find(token, offset)
        yield token, offset, offset+len(token)
        offset += len(token)

In [117]:
from tqdm import tqdm_notebook as tqdm
all_item = []

for i in tqdm(range(len(reviews))):
    word_ls = []
    #print("sentence:",i+1)
    
    for token in spans(reviews.location[i]):
        #print(token)
        #assert token[0]==reviews.location[i][token[1]:token[2]]
        my_tuple = token[0]
        #print("###",token)
        
        #my_tuples = ' , '.join(map(str, my_tuple))
        if token[0] in word_location:
            #word_ls.append(my_tuple)
            subwords = token[0].split()
            pos_list = [nltk.pos_tag([w]) for w in subwords]
            tag_list = ['I-LOC']*len(pos_list)
            tag_list[0] = 'B-LOC' 
            
            
            for s,p,t in zip(subwords,pos_list,tag_list):           
                if type(p) == list:
                    p = p[0][1]
                    #print('list')
                new_item = dict({'Sentence #': i+1, 'Tag' : t, 'Word': s,'POS': p})
                all_item.append(new_item)
                
                
            #lis_lo = nltk.pos_tag(word_ls),LOC
            #print(' , '.join(map(str, lis_lo)))
 
        elif token[0] in word_list_name:
            
            subwords = token[0].split()
            pos_list = [nltk.pos_tag([w]) for w in subwords]
            tag_list = ['I-ORG']*len(pos_list)
            tag_list[0] = 'B-ORG' 
            
            #print(subwords)
            for s,p,t in zip(subwords,pos_list,tag_list):           
                new_item = dict({'Sentence #': i+1, 'Tag' : t, 'Word': s,'POS': p[0][1]})
                all_item.append(new_item)
                #print(new_item)
            #word_ls.append(my_tuple)
            #print("found LOC")
            #lis_lo = nltk.pos_tag(word_ls),"LOC"
            #print(' , '.join(map(str, lis_lo)))
             
        elif token[0] in word_list_fac:
            #word_ls.append(my_tuple)
            #lis_lo = nltk.pos_tag(word_ls),"FACILITY"
            #print(' , '.join(map(str, lis_lo)))
            
            #my_pos = nltk.pos_tag([my_tuple])[0][1]
            #new_item =  dict({'Sentence #': i+1, 'Tag' : 'FACILITY', 'Word': my_tuple,'POS': my_pos})
            
            subwords = token[0].split()
            pos_list = [nltk.pos_tag([w]) for w in subwords]
            tag_list = ['I-FAC']*len(pos_list)
            tag_list[0] = 'B-FAC' 
            
             
            for s,p,t in zip(subwords,pos_list,tag_list):   
                if type(p) == list:
                    p = p[0][1]
                new_item = dict({'Sentence #': i+1, 'Tag' : t, 'Word': s,'POS': p})
                all_item.append(new_item)
                

             
        else:
            #print(type(my_tuple))
            my_pos = nltk.pos_tag([my_tuple])[0][1]
            new_item = dict({'Sentence #': i+1, 'Tag' : 'O', 'Word': my_tuple.lower(),'POS': my_pos})
            all_item.append(new_item)
            
            #if i+1 == 5177:
                #print(new_item)
             
            #print(nltk.pos_tag([my_tuple]),',','O')
        #print(new_item)
        #if not(my_pos == '.' or  my_pos == ',' or my_pos == ':' or my_pos == '(' or my_pos == ')') :
            
            #all_item.append(new_item) 

        

        
    

          

## 3) save preproc data

In [119]:
file_csv = 'data-loc-fac-bert.csv'
with open(file_csv, 'w') as csv_file:
    csv_file.write('Sentence #*Word*POS*Tag\n')
    for item in all_item:
        
        #print(item['POS'])    
        csv_file.write(str(item['Sentence #'])+'*'+item['Word']+'*'+item['POS']+'*'+item['Tag']+'\n')
csv_file.close()

## 4) Load preprocessed data

In [1]:
import pandas as pd
import pandas as pd
import numpy as np
from tqdm import tqdm, trange
#load data
# explore data
file_csv = 'data-loc-fac-bert.csv'
data = pd.read_csv(file_csv, sep='*',encoding="utf-8").fillna(method="ffill")

data.head(10)
 


Sentence #       Word  POS    Tag
0           1    staying  VBG      O
1           1         at   IN      O
2           1          @   NN  B-ORG
3           1       Home   NN  I-ORG
4           1  Executive   NN  I-ORG
5           1  Apartment   NN  I-ORG
6           1         is  VBZ      O
7           1          a   DT      O
8           1       good   JJ      O
9           1     choice   NN      O

### 5) BERT trained-formating

In [2]:
class SentenceGetter(object):
    
    def __init__(self, data):
        self.n_sent = 1
        self.data = data
        self.empty = False
        agg_func = lambda s: [(w, p, t) for w, p, t in zip(s["Word"].values.tolist(),
                                                           s["POS"].values.tolist(),
                                                           s["Tag"].values.tolist())]
        self.grouped = self.data.groupby("Sentence #").apply(agg_func)
        self.sentences = [s for s in self.grouped]
    
    def get_next(self):
        try:
            s = self.grouped["Sentence: {}".format(self.n_sent)]
            self.n_sent += 1
            return s
        except:
            return None

In [3]:
 
#concat sentence
getter = SentenceGetter(data)

In [4]:
word_list = [ [s[0] for s in sent] for sent in getter.sentences] 

In [5]:
sentences = word_list
sentences[0]

[u'staying',
 u'at',
 u'@',
 u'Home',
 u'Executive',
 u'Apartment',
 u'is',
 u'a',
 u'good',
 u'choice',
 u'when',
 u'you',
 u'are',
 u'visiting',
 u'Central',
 u'Pattaya',
 u'.']

In [6]:
print(len(sentences))

26541


In [7]:
labels = [[s[2] for s in sent] for sent in getter.sentences]
print(len(labels[0]))

17


In [8]:
print(len(word_list[0]))

17


In [9]:
print(len(labels))

26541


In [10]:
tags_vals = list(set(data["Tag"].values))
tag2idx = {t: i for i, t in enumerate(tags_vals)}
idx2tag = {i: t for i, t in enumerate(tags_vals) }

In [11]:
words = list(set(data["Word"].values))
n_words = len(words); 
word2idx = {w: i + 2 for i, w in enumerate(words)}
word2idx["UNK"] = 1
word2idx["PAD"] = 0
idx2word = {i: w for w, i in word2idx.items()}
n_words

14607

In [12]:
idx2tag[2]

u'B-ORG'

# Training

In [13]:
import torch
from torch.optim import Adam
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from pytorch_pretrained_bert import BertTokenizer, BertConfig
from pytorch_pretrained_bert import BertForTokenClassification, BertAdam

Using TensorFlow backend.


Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex.


In [37]:
MAX_LEN = 128
bs = 16
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

n_gpu = torch.cuda.device_count()
torch.cuda.get_device_name(0) 
torch.cuda.set_device(1)

In [38]:
tokenized_texts = word_list
print(tokenized_texts[0])

[u'staying', u'at', u'@', u'Home', u'Executive', u'Apartment', u'is', u'a', u'good', u'choice', u'when', u'you', u'are', u'visiting', u'Central', u'Pattaya', u'.']


In [52]:
sentences[0]

[u'staying',
 u'at',
 u'@',
 u'Home',
 u'Executive',
 u'Apartment',
 u'is',
 u'a',
 u'good',
 u'choice',
 u'when',
 u'you',
 u'are',
 u'visiting',
 u'Central',
 u'Pattaya',
 u'.']

### Load embedding

In [53]:
tokens_ids = [[word2idx[w] for w in s] for s in tokenized_texts]
print(len(tokens_ids[0]),len(labels[0]))

(17, 17)


In [54]:
 print(len(tokens_ids[0]),len(labels[0]))
 

(17, 17)


In [55]:
#input_ids = pad_sequences([tokenizer.convert_tokens_to_ids(txt) for txt in tokenized_texts],
input_ids = pad_sequences(tokens_ids,
                          maxlen=MAX_LEN, dtype="int64", truncating="post", padding="post")
#input_ids = pad_sequences([convert_word2idx(txt) for txt in tokenized_texts],
                          #maxlen=MAX_LEN, dtype="int64", truncating="post", padding="post")

In [56]:
print(MAX_LEN)
for i in tokens_ids:
    if len(i) > MAX_LEN:
        #print(tokens_ids)
        print("need more")
        MAX_LEN = len(i)
print(MAX_LEN)

128
128


In [57]:
t_list = [[tag2idx.get(l) for l in lab] for lab in labels]
len(t_list[0])

17

In [58]:
print(input_ids[0])

[ 8347  1718 10897  3658  3509   549  7853  5564  3823   931 11771  5312
 13274  9586  7755 11059   572     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0]


In [59]:
tags = pad_sequences([[tag2idx.get(l) for l in lab] for lab in labels],
                     maxlen=MAX_LEN, value=tag2idx["O"], padding="post",
                     dtype="int64", truncating="post")

In [60]:
attention_masks = [[float(i>0) for i in ii] for ii in input_ids]

In [62]:
#split train test
tr_inputs, val_inputs, tr_tags, val_tags = train_test_split(input_ids, tags, 
                                                            random_state=2018, test_size=0.1)
tr_masks, val_masks, _, _ = train_test_split(attention_masks, input_ids,
                                             random_state=2018, test_size=0.1)

In [63]:
#change to torhc tensor
tr_inputs = torch.tensor(tr_inputs)
val_inputs = torch.tensor(val_inputs)
tr_tags = torch.tensor(tr_tags)
val_tags = torch.tensor(val_tags)
tr_masks = torch.tensor(tr_masks)
val_masks = torch.tensor(val_masks)

In [64]:
print(tr_inputs.shape)
print(tr_masks.shape)
print(tr_tags.shape)

torch.Size([23886, 128])
torch.Size([23886, 128])
torch.Size([23886, 128])


In [65]:
print(val_inputs.shape)
print(val_masks.shape)
print(val_tags.shape)

torch.Size([2655, 128])
torch.Size([2655, 128])
torch.Size([2655, 128])


In [66]:
train_data = TensorDataset(tr_inputs, tr_masks, tr_tags)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=bs)

valid_data = TensorDataset(val_inputs, val_masks, val_tags)
valid_sampler = SequentialSampler(valid_data)
valid_dataloader = DataLoader(valid_data, sampler=valid_sampler, batch_size=bs)

In [67]:
print(len(tag2idx))

7


In [68]:
model = BertForTokenClassification.from_pretrained(u"bert-base-uncased", num_labels=len(tag2idx))

In [69]:
model.cuda();

In [70]:
FULL_FINETUNING = True
if FULL_FINETUNING:
    param_optimizer = list(model.named_parameters())
    no_decay = ['bias', 'gamma', 'beta']
    optimizer_grouped_parameters = [
        {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)],
         'weight_decay_rate': 0.01},
        {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)],
         'weight_decay_rate': 0.0}
    ]
else:
    param_optimizer = list(model.classifier.named_parameters()) 
    optimizer_grouped_parameters = [{"params": [p for n, p in param_optimizer]}]
optimizer = Adam(optimizer_grouped_parameters, lr=3e-5)

In [71]:
#Fine tune BERT
from seqeval.metrics import f1_score

def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=2).flatten()
    labels_flat = labels.flatten()
    return np.sum(pred_flat == labels_flat) / len(labels_flat) 

In [81]:
epochs = 10
max_grad_norm = 1.0

for _ in trange(epochs, desc="Epoch"):
    # TRAIN loop
    model.train()
    tr_loss = 0
    nb_tr_examples, nb_tr_steps = 0, 0
    for step, batch in enumerate(train_dataloader):
        # add batch to gpu
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
        # forward pass
        loss = model(b_input_ids, token_type_ids=None,
                     attention_mask=b_input_mask, labels=b_labels)
        # backward pass
        loss.backward()
        # track train loss
        tr_loss += loss.item()
        nb_tr_examples += b_input_ids.size(0)
        nb_tr_steps += 1
        # gradient clipping
        torch.nn.utils.clip_grad_norm_(parameters=model.parameters(), max_norm=max_grad_norm)
        # update parameters
        optimizer.step()
        model.zero_grad()
    # print train loss per epoch
    print("Train loss: {}".format(tr_loss/nb_tr_steps))
    # VALIDATION on validation set
    model.eval()
    eval_loss, eval_accuracy = 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0
    predictions , true_labels, true_inputs = [], [],[]
    for batch in valid_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
        
        with torch.no_grad():
            tmp_eval_loss = model(b_input_ids, token_type_ids=None,
                                  attention_mask=b_input_mask, labels=b_labels)
            logits = model(b_input_ids, token_type_ids=None,
                           attention_mask=b_input_mask)
        logits = logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
        inputs = b_input_ids.to('cpu').numpy()
         
        true_inputs.append(inputs)
        predictions.extend([list(p) for p in np.argmax(logits, axis=2)])
        true_labels.append(label_ids)
        
        tmp_eval_accuracy = flat_accuracy(logits, label_ids)
        
        eval_loss += tmp_eval_loss.mean().item()
        eval_accuracy += tmp_eval_accuracy
        
        nb_eval_examples += b_input_ids.size(0)
        nb_eval_steps += 1
    eval_loss = eval_loss/nb_eval_steps
    print("Validation loss: {}".format(eval_loss))
    print("Validation Accuracy: {}".format(eval_accuracy/nb_eval_steps))
    pred_tags = [tags_vals[p_i] for p in predictions for p_i in p]
    valid_tags = [tags_vals[l_ii] for l in true_labels for l_i in l for l_ii in l_i]
    valid_inputs = [[idx2word[l_ii] for l_ii in l_i] for l in  true_inputs  for l_i in l ]


    print("F1-Score: {}".format(f1_score(pred_tags, valid_tags)))


Epoch:   0%|          | 0/10 [00:00<?, ?it/s]

Train loss: 0.00117779640816
Validation loss: 0.00733748172084
Validation Accuracy: 0



Epoch:  10%|█         | 1/10 [06:31<58:40, 391.20s/it]

F1-Score: 0.255037145967
Train loss: 0.00128043145534
Validation loss: 0.00998011574533
Validation Accuracy: 0



Epoch:  20%|██        | 2/10 [13:08<52:23, 392.95s/it]

...

F1-Score: 0.323244756595
Train loss: 0.000721595064803
Validation loss: 0.00776051912019
Validation Accuracy: 0



Epoch:  90%|█████████ | 9/10 [59:29<06:36, 396.75s/it]

F1-Score: 0.287365671961
Train loss: 0.000700116623798
Validation loss: 0.00723314021249
Validation Accuracy: 0



Epoch: 100%|██████████| 10/10 [1:06:06<00:00, 396.60s/it]

F1-Score: 0.224291772689


In [84]:
count = 0 
all_data = 0
for i,j,ll in zip(pred_tags,valid_tags,val_inputs):
    for k,l,kk in zip(i,j,ll):
        if k==l   : 
            count += 1
            print(k,l,idx2word[kk.item()])
        all_data += 1
print(count)
print(all_data)

(u'B', u'B', u'Pattara')
(u'-', u'-', u'Place')
(u'O', u'O', u'Hotel')
(u'R', u'R', u',')
(u'G', u'G', u'Chiang')
(u'I', u'I', u'with')
(u'-', u'-', u'you')
(u'O', u'O', u'stay')
(u'R', u'R', u'at')
(u'G', u'G', u'Butterfly')
(u'I', u'I', u'with')
(u'-', u'-', u'you')
(u'O', u'O', u'stay')
(u'R', u'R', u'at')
(u'G', u'G', u'Sawasdee')
(u'O', u'O', u'for')
(u'B', u'B', u'with')
(u'-', u'-', u'you')
(u'L', u'L', u'stay')
(u'O', u'O', u'at')
(u'C', u'C', u'The')
(u'I', u'I', u'Pandora')
(u'-', u'-', u'Lifestyle')
(u'L', u'L', u'Hotel')
(u'O', u'O', u',')
(u'C', u'C', u'ko')
(u'O', u'O', u'CHAMBERTIN')
(u'O', u'O', u'for')
(u'O', u'O', u'The')
(u'O', u'O', u'staying')
(u'O', u'O', u'PapaCrab')
(u'O', u'O', u'The')
(u'O', u'O', u'with')
(u'O', u'O', u'Link')
(u'O', u'O', u'with')
(u'O', u'O', u'staying')
(u'O', u'O', u'with')
(u'O', u'O', u'with')
(u'O', u'O', u'with')
(u'O', u'O', u'Oscar')
(u'O', u'O', u'Boutique')
(u'O', u'O', u'with')
(u'O', u'O', u'Surasak')
(u'O', u'O', u'Anissa')
(u'

(u'I', u'I', u'Chiangkham')
(u'-', u'-', u'Luang')
(u'L', u'L', u'Resort')
(u'O', u'O', u'is')
(u'C', u'C', u'located')
(u'O', u'O', u'for')
(u'B', u'B', u'Pro')
(u'-', u'-', u'Andaman')
(u'L', u'L', u'Place')
(u'O', u'O', u'is')
(u'C', u'C', u'a')
(u'I', u'I', u'Paripas')
(u'-', u'-', u'Express')
(u'L', u'L', u'Patong')
(u'O', u'O', u'Hotel')
(u'C', u'C', u',')
(u'I', u'I', u'with')
(u'-', u'-', u'you')
(u'L', u'L', u'stay')
(u'O', u'O', u'at')
(u'C', u'C', u'Tanee')
(u'O', u'O', u'Patong')
(u'B', u'B', u'with')
(u'-', u'-', u'you')
(u'L', u'L', u'stay')
(u'O', u'O', u'at')
(u'C', u'C', u'Sunshine')
(u'O', u'O', u'rosie')
(u'B', u'B', u'for')
(u'-', u'-', u'the')
(u'L', u'L', u'comfort')
(u'O', u'O', u'and')
(u'C', u'C', u'convenience')
(u'O', u'O', u'staying')
(u'O', u'O', u'for')
(u'O', u'O', u'with')
(u'O', u'O', u'Bangkok')
(u'O', u'O', u'Saiyuan')
(u'O', u'O', u'Sivana')
(u'O', u'O', u'with')
(u'O', u'O', u'Cocooning')
(u'O', u'O', u'Capricorn')
(u'O', u'O', u'with')
(u'O', u'O',

In [85]:
#evaluate model
model.eval()
predictions = []
true_labels = []
true_inputs = []

eval_loss, eval_accuracy = 0, 0
nb_eval_steps, nb_eval_examples = 0, 0
print(len(valid_dataloader))
for batch in tqdm(valid_dataloader):
    #print(len(batch))
    batch = tuple(t.to(device) for t in batch)
    b_input_ids, b_input_mask, b_labels = batch

    with torch.no_grad():
        tmp_eval_loss = model(b_input_ids, token_type_ids=None,
                              attention_mask=b_input_mask, labels=b_labels)
        logits = model(b_input_ids, token_type_ids=None,
                       attention_mask=b_input_mask)
        
    logits = logits.detach().cpu().numpy()
    predictions.extend([list(p) for p in np.argmax(logits, axis=2)])
    label_ids = b_labels.to('cpu').numpy()
    inputs = b_input_ids.to('cpu').numpy()
    true_inputs.append(inputs)
    
    
    true_labels.append(label_ids)
    tmp_eval_accuracy = flat_accuracy(logits, label_ids)

    eval_loss += tmp_eval_loss.mean().item()
    eval_accuracy += tmp_eval_accuracy

    nb_eval_examples += b_input_ids.size(0)
    nb_eval_steps += 1

pred_tags = [[tags_vals[p_i] for p_i in p] for p in predictions]
valid_tags = [[tags_vals[l_ii] for l_ii in l_i] for l in true_labels for l_i in l ]
valid_inputs = [[idx2word[l_ii] for l_ii in l_i] for l in  true_inputs  for l_i in l ]

print("Validation loss: {}".format(eval_loss/nb_eval_steps))
print("Validation Accuracy: {}".format(eval_accuracy/nb_eval_steps))
print("Validation F1-Score: {}".format(f1_score(pred_tags, valid_tags)))


  1%|          | 1/166 [00:00<00:24,  6.81it/s]

166



 95%|█████████▍| 157/166 [00:20<00:01,  7.75it/s]


100%|██████████| 166/166 [00:21<00:00,  7.82it/s]

Validation loss: 0.00723314021249
Validation Accuracy: 0
Validation F1-Score: 0.224291772689


In [86]:
count = 0 
all_data = 0
for i,j,ll in zip(pred_tags,valid_tags,val_inputs):
    for k,l,kk in zip(i,j,ll):
        if k==l   : 
            count += 1
            print(k,l,idx2word[kk.item()])
        all_data += 1
print(count)
print(all_data)

(u'B-ORG', u'B-ORG', u'Pattara')
(u'I-ORG', u'I-ORG', u'Place')
(u'I-ORG', u'I-ORG', u'Hotel')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Chiang')
(u'I-LOC', u'I-LOC', u'Mai')
(u'O', u'O', u'are')
(u'O', u'O', u'right')
(u'O', u'O', u'in')
(u'O', u'O', u'the')
(u'O', u'O', u'comfort')
(u'O', u'O', u'of')
(u'O', u'O', u'your')
(u'O', u'O', u'own')
(u'O', u'O', u'home')
(u'O', u'O', u'and')
(u'O', u'O', u'the')
(u'O', u'O', u'property')
(u'O', u'O', u'offers')
(u'O', u'O', u'fantastic')
(u'O', u'O', u'facilities')
(u'O', u'O', u',')
(u'O', u'O', u'including')
(u'O', u'O', u'free')
(u'B-FAC', u'B-FAC', u'Parking')
(u'O', u'O', u',')
(u'O', u'O', u'free')
(u'O', u'O', u'high')
(u'O', u'O', u'speed')
(u'O', u'O', u'internet')
(u'O', u'O', u'(')
(u'B-FAC', u'B-FAC', u'WiFi')
(u'O', u'O', u')')
(u'O', u'O', u',')
(u'O', u'O', u'room')
(u'O', u'O', u'service')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PA

(u'O', u'O', u'at')
(u'O', u'O', u's.b')
(u'O', u'O', u'.')
(u'O', u'O', u'mansion')
(u'O', u'O', u'lodge')
(u'O', u'O', u',')
(u'O', u'O', u'krabi/ao')
(u'O', u'O', u'nang')
(u'O', u'O', u'the')
(u'O', u'O', u'hotel')
(u'O', u'O', u'has')
(u'O', u'O', u'a')
(u'O', u'O', u'very')
(u'O', u'O', u'good')
(u'O', u'O', u'location')
(u'O', u'O', u',')
(u'O', u'O', u'also')
(u'O', u'O', u'near')
(u'O', u'O', u'buzz')
(u'O', u'O', u'organic')
(u'O', u'O', u'food')
(u'O', u'O', u'&')
(u'O', u'O', u'drink,11/1')
(u'O', u'O', u'thaifood')
(u'O', u'O', u'&')
(u'O', u'O', u'cocktail')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Aonang')
(u'I-LOC', u'I-LOC', u'Buffet')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Bawarchi')
(u'I-LOC', u'I-LOC', u'Delight')
(u'O', u'O', u',')
(u'O', u'O', u'get')
(u'O', u'O', u'rad')
(u'O', u'O', u"'s")
(u'O', u'O', u',')
(u'O', u'O', u'roots')
(u'O', u'O', u'rock')
(u'O', u'O', u'reggae')
(u'B-FAC', u'B-FAC', u'Bar')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Ao')
(u'I-LO

(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'B-ORG', u'B-ORG', u'Mad')
(u'I-ORG', u'I-ORG', u'Panda')
(u'I-ORG', u'I-ORG', u'Hostel')
(u'I-ORG', u'I-ORG', u'Huahin')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Hua')
(u'I-LOC', u'I-LOC', u'Hin')
(u'O', u'O', u'are')
(u'O', u'O', u'right')
(u'O', u'O', u'in')
(u'O', u'O', u'the')
(u'O', u'O', u'comfort')
(u'O', u'O', u'of')
(u'O', u'O', u'your')
(u'O', u'O', u'own')
(u'O', u'O', u'home')
(u'O', u'O', u'and')
(u'O', u'O', u'the')
(u'O', u'O', u'property')
(u'O', u'O', u'offers')
(u'O', u'O', u'fantastic')
(u'O', u'O', u'facilities')
(u'O', u'O', u','

(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Pagoda')
(u'I-LOC', u'I-LOC', u'Chinese')
(u'I-LOC', u'I-LOC', u'Restaurant')
(u'O', u'O', u',')
(u'O', u'O', u'crossfit')
(u'B-LOC', u'B-LOC', u'Bangkok')
(u'O', u'O', u'(')
(u'O', u'O', u'cfbk')
(u'O', u'O', u')')
(u'O', u'O', u',')
(u'O', u'O', u'dasa')
(u'O', u'O', u'book')
(u'B-FAC', u'B-FAC', u'Cafe')
(u'O', u'O', u',')
(u'O', u'O', u'vanilla')
(u'O', u'O', u'sky')
(u'O', u'O', u'rooftop')
(u'B-FAC', u'B-FAC', u'Bar')
(u'O', u'O', u'-')
(u'B-ORG', u'B-ORG', u'Compass')
(u'I-ORG', u'I-ORG', u'Skyview')
(u'I-ORG', u'I-ORG', u'Hotel')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Suvarnabhumi')
(u'I-LOC', u'I-LOC', u'Intl')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Don')
(u'I-LOC', u'I-LOC', u'Muang')
(u'I-LOC', u'I-LOC', u'Airport')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Phrom')
(u'I-LOC', u'I-LOC', u'Phong')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Queen')
(u'I-LOC', u'I-LOC', u'Sirikit')
(u'I-LOC', u'I-LOC', u'National')
(u'I-LOC', u'I-LO

(u'I-ORG', u'I-ORG', u'Inn')
(u'I-ORG', u'I-ORG', u'Villa')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Bangkok')
(u'O', u'O', u'are')
(u'O', u'O', u'right')
(u'O', u'O', u'in')
(u'O', u'O', u'the')
(u'O', u'O', u'comfort')
(u'O', u'O', u'of')
(u'O', u'O', u'your')
(u'O', u'O', u'own')
(u'O', u'O', u'home')
(u'O', u'O', u'and')
(u'O', u'O', u'the')
(u'O', u'O', u'property')
(u'O', u'O', u'offers')
(u'O', u'O', u'fantastic')
(u'O', u'O', u'facilities')
(u'O', u'O', u',')
(u'O', u'O', u'including')
(u'O', u'O', u'free')
(u'O', u'O', u'high')
(u'O', u'O', u'speed')
(u'O', u'O', u'internet')
(u'O', u'O', u'(')
(u'B-FAC', u'B-FAC', u'WiFi')
(u'O', u'O', u')')
(u'O', u'O', u',')
(u'B-FAC', u'B-FAC', u'Laundry')
(u'O', u'O', u'service')
(u'O', u'O', u',')
(u'O', u'O', u'non-smoking')
(u'O', u'O', u'hotel')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O'

...

(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', u'for')
(u'O', u'O', u'the')
(u'O', u'O', u'comfort')
(u'O', u'O', u'and')
(u'O', u'O', u'convenience')
(u'O', u'O', u'of')
(u'O', u'O', u'guests')
(u'O', u'O', u',')
(u'B-ORG', u'B-ORG', u'Koh')
(u'I-ORG', u'I-ORG', u'Si')
(u'I-ORG', u'I-ORG', u'Chang')
(u'I-ORG', u

(u'O', u'O', u'all')
(u'O', u'O', u'tastes')
(u'O', u'O', u',')
(u'O', u'O', u'and')
(u'O', u'O', u'many')
(u'O', u'O', u'facilities')
(u'O', u'O', u'such')
(u'O', u'O', u'as')
(u'O', u'O', u'room')
(u'O', u'O', u'service')
(u'O', u'O', u',')
(u'O', u'O', u'free')
(u'B-FAC', u'B-FAC', u'Parking')
(u'O', u'O', u',')
(u'B-FAC', u'B-FAC', u'Restaurant')
(u'O', u'O', u',')
(u'O', u'O', u'bar/lounge')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')


(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'B-ORG', u'B-ORG', u'House23')
(u'I-ORG', u'I-ORG', u'Lodge')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Bangkok')
(u'O', u'O', u'are')
(u'O', u'O', u'right')
(u'O', u'O', u'in')
(u'O', u'O', u'the')
(u'O', u'O', u'comfort')
(u'O', u'O', u'of')
(u'O', u'O', u'your')
(u'O', u'O', u'own')
(u'O', u'O', u'home')
(u'O', u'O', u'and')
(u'O', u'O', u'the')
(u'O', u'O', u'property')
(u'O', u'O', u'offers')
(u'O', u'O', u'fantastic')
(u'O', u'O', u'facilities')
(u'O', u'O', u',')
(u'O', u'O', u'including')
(u'O', u'O', u'f

(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'O', u'O', 'PAD')
(u'B-ORG', u'B-ORG', u'Holly')
(u'I-ORG', u'I-ORG', u'House')
(u'I-ORG', u'I-ORG', u'Hostel')
(u'O', u'O', u',')
(u'B-LO

(u'O', u'O', u'you')
(u'O', u'O', u'stay')
(u'O', u'O', u'at')
(u'B-ORG', u'B-ORG', u'On')
(u'I-ORG', u'I-ORG', u'the')
(u'I-ORG', u'I-ORG', u'Hill')
(u'I-ORG', u'I-ORG', u'Karon')
(u'I-ORG', u'I-ORG', u'Resort')
(u'I-ORG', u'I-ORG', u'Hotel')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Phuket')
(u'O', u'O', u'the')
(u'O', u'O', u'hotel')
(u'O', u'O', u'has')
(u'O', u'O', u'a')
(u'O', u'O', u'very')
(u'O', u'O', u'good')
(u'O', u'O', u'location')
(u'O', u'O', u',')
(u'O', u'O', u'also')
(u'O', u'O', u'near')
(u'B-LOC', u'B-LOC', u'Sabaijai')
(u'I-LOC', u'I-LOC', u'Cafe')
(u'O', u'O', u',')
(u'O', u'O', u'coast')
(u'O', u'O', u'beach')
(u'O', u'O', u'club')
(u'O', u'O', u'&')
(u'O', u'O', u'bistro')
(u'B-LOC', u'B-LOC', u'Phuket')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'Sweet')
(u'I-LOC', u'I-LOC', u'and')
(u'I-LOC', u'I-LOC', u'Sour')
(u'O', u'O', u',')
(u'B-LOC', u'B-LOC', u'The')
(u'I-LOC', u'I-LOC', u'Dining')
(u'I-LOC', u'I-LOC', u'Room')
(u'I-LOC', u'I-LOC', u'at')
(u'I-LOC', u'I-

for lab in b_labels:
    for l in lab:
        print(idx2tag[int(l)])
        

In [87]:
print(count)
print(all_data)

213791
339840
